In [37]:
%matplotlib inline
import pandas as pd
import numpy as np
import re
from sklearn import preprocessing
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import stopwords
import nltk
from sklearn.feature_extraction.text import CountVectorizer
from nltk.stem.wordnet import WordNetLemmatizer 
import json
import itertools
import datetime 
from sklearn.preprocessing import OneHotEncoder
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.common.exceptions import NoSuchElementException, StaleElementReferenceException
import time
import json
import datetime
from collections import Counter

In [38]:
# path variables for KEVIN

path = "D:\Kevin Liang/Documents/1_UT_SENIOR/UT_AUSTIN_FALL_2017/EE_379K/Data_Science_Final_Project/Kickstarter_Data/"

In [39]:
def search_results(query):
    browser = webdriver.Firefox()
    browser.get(query)
    time.sleep(1)
    body = browser.find_element_by_tag_name('body')
    while True:
        elemsCount = browser.execute_script("return document.querySelectorAll('.stream-items > li.stream-item').length")

        browser.execute_script("window.scrollTo(0, document.body.scrollHeight);")

        try:
            WebDriverWait(browser, 20).until(
                lambda x: x.find_element_by_xpath(
                    "//*[contains(@class,'stream-items')]/li[contains(@class,'stream-item')]["+str(elemsCount+1)+"]"))
        except:
            break

    errors = browser.find_elements_by_class_name('center')
    for error in errors:
        if (error.text == "Sorry! This person is no longer active on Kickstarter."):
            browser.quit()
            return 0, 0

    price = browser.find_elements_by_class_name('count')
    check = False
    for val in price:
        count = val.text
        count =count.encode('utf-8')
        if (check == True):
            num_backed= count
            check = False
        else:
            num_created = count
            check = True
            
    '''  
    projects = browser.find_elements_by_class_name('backed')
    for project in projects:
        text = project.text
        words = text.split()
        num_backed = str(words[1])
        #print num_backed
        browser.quit()
        
    '''  
    
    return int(num_backed), int(num_created)

In [40]:
def add_user_profile_data(df):
    user_num_backers = []
    user_num_creators = []
    
    for user_url in df['user_profiles']:
        b, c = search_results(user_url)
        user_num_backers.append(b)
        user_num_creators.append(c)
    
    df['user_num_backers'] = pd.Series(user_num_backers)
    df['user_num_creators'] = pd.Series(user_num_creators)
    
    return df

In [41]:
# data - Data set
# feature - feature that is going to be processed using nlp

def nlp_data(data, feature, total_words):
    all_words = []
    regex_word = "[^a-zA-Z]"
    lem = WordNetLemmatizer()

    for cell_data in data[feature]:
        words = re.sub(regex_word," ",cell_data).lower().split()
        words = [i for i in words if not i in stopwords.words('english')]
        # might change len of word
        words = [i for i in words if len(i) > 1]
        words = [lem.lemmatize(i, "v") for i in words]
        words = [lem.lemmatize(i) for i in words]
        all_words += words

    vectorizer = CountVectorizer(analyzer = "word", stop_words = "english", max_features = total_words)
    word_count = vectorizer.fit_transform(all_words).toarray()
    final_words = vectorizer.get_feature_names()
    
    return final_words

In [42]:
def preprocess_nlp(data, feature):
    word_list = []
    regex_word = "[^a-zA-Z]"
    lem = WordNetLemmatizer()
    for i in data[feature]:
        words = re.sub(regex_word," ",i).lower().split()
        words = [i for i in words if not i in stopwords.words('english')]
        # might change len of word
        words = [i for i in words if len(i) > 1]
        words = [lem.lemmatize(i, "v") for i in words]
        words = [lem.lemmatize(i) for i in words]
        word_list.append(words)
    data.drop(feature, axis = 1)
    data[feature] = word_list
    return data

In [43]:
def nlp(data, list_of_features, total_words):
    for i in list_of_features:
        final_words = nlp_data(data, i, total_words)
        print "final_words"
        data = preprocess_nlp(data,i)
        print "preprocess"
        nlp_features = []
        for index, word in enumerate(final_words):
            lst = []
            for x in data[i]:
                lst.append(x.count(word))
            nlp_features.append(lst)
            print(str(word) + " : " + str(index))
            
        nlp_features = np.array(nlp_features)
        nlp_features_column = np.array(nlp_features).T
        nlp_feature_data = pd.DataFrame(data = nlp_features_column, columns = final_words)
        data = data.drop(i, axis = 1)
        data = pd.concat([data, nlp_feature_data], axis = 1)
    return data

In [44]:
# data - dataset as a DataFrame object
# list_of_features - features that need to be one hot encoded

def ohe_data(data, list_of_features):
    ohe = data[list_of_features]
    new_data = data.drop(list_of_features, axis = 1)
    ohe_features = pd.get_dummies(ohe)
    return pd.concat([new_data,ohe_features], axis = 1)

In [45]:
def json_creator_parser(data):
    new_feature = []
    for i in range(data["creator"].shape[0]):
        json_parsed_data = json.loads(data["creator"].iloc[i])
        new_feature.append(json_parsed_data['urls']['web']['user'])
        print "creator:" + str(i)
        
    new_data = data.drop('creator', axis = 1)
    new_data["user_profiles"] = new_feature
    return new_data


In [46]:
def json_category_parser(data):
    new_feature_category = []
    new_feature_subcategory = []
    for i in range(data["category"].shape[0]):
        json_parsed_data = json.loads(data['category'].iloc[i])
        new_feature_category.append(json_parsed_data['slug'].split('/')[0])
        new_feature_subcategory.append(json_parsed_data['slug'].split('/')[1])
        print "category:" + str(i)
        
        
    new_data = data.drop('category', axis = 1)
    new_data["category"] = new_feature_category
    new_data["subcategory"] = new_feature_subcategory
    return new_data

In [47]:
#Verifying data authenticity
def nlp_clean(data, feature):
    i = 0
    new_data = data

    for cell_data in data[feature]:
        if(type(cell_data) != str):
            print "Not a string at row :" + str(i) + ". Removing this row"
            new_data = new_data.drop([i]).reset_index(drop=True)
        else:
            i+=1
    return new_data

In [48]:
data = pd.read_csv(path + "combined_data.csv", header = 0, index_col = 0)
data = data.drop(["photo", "urls","source_url","location"], axis = 1)
total_time = abs(data["launched_at"] - data["deadline"])
data["total_time"] = total_time
nlp_features = ["blurb","name"]
ohe_features = ["state","disable_communication","country","currency", "currency_trailing_code","is_starrable","current_currency","usd_type"]

In [49]:
print "Cleaning by Blurb:"
data = nlp_clean(data, "blurb")
print "\nDone Cleaning Blurb"
print "\nCleaning by Name:"
data = nlp_clean(data, "name")
print "\nDone Cleaning by Name"

Cleaning by Blurb:
Not a string at row :5045. Removing this row
Not a string at row :5101. Removing this row
Not a string at row :9971. Removing this row
Not a string at row :14865. Removing this row
Not a string at row :20158. Removing this row
Not a string at row :37511. Removing this row
Not a string at row :70177. Removing this row
Not a string at row :78850. Removing this row
Not a string at row :147250. Removing this row
Not a string at row :156920. Removing this row

Done Cleaning Blurb

Cleaning by Name:

Done Cleaning by Name


In [50]:
data.shape

(157117, 20)

In [51]:
data = nlp(data,nlp_features, 100)
data = ohe_data(data, ohe_features)
data = json_category_parser(data)
data = json_creator_parser(data)
#data = add_user_profile_data(data)


final_words
preprocess
adventure : 0
album : 1
app : 2
art : 3
artist : 4
band : 5
base : 6
beautiful : 7
best : 8
book : 9
bring : 10
build : 11
card : 12
cd : 13
change : 14
child : 15
city : 16
collection : 17
come : 18
comedy : 19
comic : 20
community : 21
create : 22
day : 23
design : 24
dream : 25
experience : 26
family : 27
feature : 28
film : 29
food : 30
free : 31
friend : 32
fun : 33
fund : 34
game : 35
great : 36
hand : 37
help : 38
high : 39
home : 40
inspire : 41
journey : 42
kid : 43
learn : 44
let : 45
life : 46
like : 47
live : 48
local : 49
look : 50
love : 51
make : 52
man : 53
money : 54
music : 55
need : 56
new : 57
old : 58
open : 59
original : 60
paint : 61
people : 62
place : 63
play : 64
print : 65
produce : 66
project : 67
quality : 68
raise : 69
real : 70
record : 71
release : 72
series : 73
set : 74
share : 75
short : 76
small : 77
song : 78
space : 79
start : 80
story : 81
student : 82
studio : 83
style : 84
support : 85
time : 86
travel : 87
try : 88
unique

category:497
category:498
category:499
category:500
category:501
category:502
category:503
category:504
category:505
category:506
category:507
category:508
category:509
category:510
category:511
category:512
category:513
category:514
category:515
category:516
category:517
category:518
category:519
category:520
category:521
category:522
category:523
category:524
category:525
category:526
category:527
category:528
category:529
category:530
category:531
category:532
category:533
category:534
category:535
category:536
category:537
category:538
category:539
category:540
category:541
category:542
category:543
category:544
category:545
category:546
category:547
category:548
category:549
category:550
category:551
category:552
category:553
category:554
category:555
category:556
category:557
category:558
category:559
category:560
category:561
category:562
category:563
category:564
category:565
category:566
category:567
category:568
category:569
category:570
category:571
category:572
category:573

category:1142
category:1143
category:1144
category:1145
category:1146
category:1147
category:1148
category:1149
category:1150
category:1151
category:1152
category:1153
category:1154
category:1155
category:1156
category:1157
category:1158
category:1159
category:1160
category:1161
category:1162
category:1163
category:1164
category:1165
category:1166
category:1167
category:1168
category:1169
category:1170
category:1171
category:1172
category:1173
category:1174
category:1175
category:1176
category:1177
category:1178
category:1179
category:1180
category:1181
category:1182
category:1183
category:1184
category:1185
category:1186
category:1187
category:1188
category:1189
category:1190
category:1191
category:1192
category:1193
category:1194
category:1195
category:1196
category:1197
category:1198
category:1199
category:1200
category:1201
category:1202
category:1203
category:1204
category:1205
category:1206
category:1207
category:1208
category:1209
category:1210
category:1211
category:1212
catego

category:1750
category:1751
category:1752
category:1753
category:1754
category:1755
category:1756
category:1757
category:1758
category:1759
category:1760
category:1761
category:1762
category:1763
category:1764
category:1765
category:1766
category:1767
category:1768
category:1769
category:1770
category:1771
category:1772
category:1773
category:1774
category:1775
category:1776
category:1777
category:1778
category:1779
category:1780
category:1781
category:1782
category:1783
category:1784
category:1785
category:1786
category:1787
category:1788
category:1789
category:1790
category:1791
category:1792
category:1793
category:1794
category:1795
category:1796
category:1797
category:1798
category:1799
category:1800
category:1801
category:1802
category:1803
category:1804
category:1805
category:1806
category:1807
category:1808
category:1809
category:1810
category:1811
category:1812
category:1813
category:1814
category:1815
category:1816
category:1817
category:1818
category:1819
category:1820
catego

category:2380
category:2381
category:2382
category:2383
category:2384
category:2385
category:2386
category:2387
category:2388
category:2389
category:2390
category:2391
category:2392
category:2393
category:2394
category:2395
category:2396
category:2397
category:2398
category:2399
category:2400
category:2401
category:2402
category:2403
category:2404
category:2405
category:2406
category:2407
category:2408
category:2409
category:2410
category:2411
category:2412
category:2413
category:2414
category:2415
category:2416
category:2417
category:2418
category:2419
category:2420
category:2421
category:2422
category:2423
category:2424
category:2425
category:2426
category:2427
category:2428
category:2429
category:2430
category:2431
category:2432
category:2433
category:2434
category:2435
category:2436
category:2437
category:2438
category:2439
category:2440
category:2441
category:2442
category:2443
category:2444
category:2445
category:2446
category:2447
category:2448
category:2449
category:2450
catego

...

creator:154816
creator:154817
creator:154818
creator:154819
creator:154820
creator:154821
creator:154822
creator:154823
creator:154824
creator:154825
creator:154826
creator:154827
creator:154828
creator:154829
creator:154830
creator:154831
creator:154832
creator:154833
creator:154834
creator:154835
creator:154836
creator:154837
creator:154838
creator:154839
creator:154840
creator:154841
creator:154842
creator:154843
creator:154844
creator:154845
creator:154846
creator:154847
creator:154848
creator:154849
creator:154850
creator:154851
creator:154852
creator:154853
creator:154854
creator:154855
creator:154856
creator:154857
creator:154858
creator:154859
creator:154860
creator:154861
creator:154862
creator:154863
creator:154864
creator:154865
creator:154866
creator:154867
creator:154868
creator:154869
creator:154870
creator:154871
creator:154872
creator:154873
creator:154874
creator:154875
creator:154876
creator:154877
creator:154878
creator:154879
creator:154880
creator:154881
creator:15

creator:155377
creator:155378
creator:155379
creator:155380
creator:155381
creator:155382
creator:155383
creator:155384
creator:155385
creator:155386
creator:155387
creator:155388
creator:155389
creator:155390
creator:155391
creator:155392
creator:155393
creator:155394
creator:155395
creator:155396
creator:155397
creator:155398
creator:155399
creator:155400
creator:155401
creator:155402
creator:155403
creator:155404
creator:155405
creator:155406
creator:155407
creator:155408
creator:155409
creator:155410
creator:155411
creator:155412
creator:155413
creator:155414
creator:155415
creator:155416
creator:155417
creator:155418
creator:155419
creator:155420
creator:155421
creator:155422
creator:155423
creator:155424
creator:155425
creator:155426
creator:155427
creator:155428
creator:155429
creator:155430
creator:155431
creator:155432
creator:155433
creator:155434
creator:155435
creator:155436
creator:155437
creator:155438
creator:155439
creator:155440
creator:155441
creator:155442
creator:15

creator:155937
creator:155938
creator:155939
creator:155940
creator:155941
creator:155942
creator:155943
creator:155944
creator:155945
creator:155946
creator:155947
creator:155948
creator:155949
creator:155950
creator:155951
creator:155952
creator:155953
creator:155954
creator:155955
creator:155956
creator:155957
creator:155958
creator:155959
creator:155960
creator:155961
creator:155962
creator:155963
creator:155964
creator:155965
creator:155966
creator:155967
creator:155968
creator:155969
creator:155970
creator:155971
creator:155972
creator:155973
creator:155974
creator:155975
creator:155976
creator:155977
creator:155978
creator:155979
creator:155980
creator:155981
creator:155982
creator:155983
creator:155984
creator:155985
creator:155986
creator:155987
creator:155988
creator:155989
creator:155990
creator:155991
creator:155992
creator:155993
creator:155994
creator:155995
creator:155996
creator:155997
creator:155998
creator:155999
creator:156000
creator:156001
creator:156002
creator:15

creator:156497
creator:156498
creator:156499
creator:156500
creator:156501
creator:156502
creator:156503
creator:156504
creator:156505
creator:156506
creator:156507
creator:156508
creator:156509
creator:156510
creator:156511
creator:156512
creator:156513
creator:156514
creator:156515
creator:156516
creator:156517
creator:156518
creator:156519
creator:156520
creator:156521
creator:156522
creator:156523
creator:156524
creator:156525
creator:156526
creator:156527
creator:156528
creator:156529
creator:156530
creator:156531
creator:156532
creator:156533
creator:156534
creator:156535
creator:156536
creator:156537
creator:156538
creator:156539
creator:156540
creator:156541
creator:156542
creator:156543
creator:156544
creator:156545
creator:156546
creator:156547
creator:156548
creator:156549
creator:156550
creator:156551
creator:156552
creator:156553
creator:156554
creator:156555
creator:156556
creator:156557
creator:156558
creator:156559
creator:156560
creator:156561
creator:156562
creator:15

creator:157057
creator:157058
creator:157059
creator:157060
creator:157061
creator:157062
creator:157063
creator:157064
creator:157065
creator:157066
creator:157067
creator:157068
creator:157069
creator:157070
creator:157071
creator:157072
creator:157073
creator:157074
creator:157075
creator:157076
creator:157077
creator:157078
creator:157079
creator:157080
creator:157081
creator:157082
creator:157083
creator:157084
creator:157085
creator:157086
creator:157087
creator:157088
creator:157089
creator:157090
creator:157091
creator:157092
creator:157093
creator:157094
creator:157095
creator:157096
creator:157097
creator:157098
creator:157099
creator:157100
creator:157101
creator:157102
creator:157103
creator:157104
creator:157105
creator:157106
creator:157107
creator:157108
creator:157109
creator:157110
creator:157111
creator:157112
creator:157113
creator:157114
creator:157115
creator:157116
two


In [55]:
data = ohe_data(data, ["category","subcategory"])

In [56]:
data.to_csv(path + "final_data.csv")

In [57]:
data.isnull().sum()

goal                             0
pledged                          0
deadline                         0
created_at                       0
launched_at                      0
usd_pledged                      0
converted_pledged_amount         0
total_time                       0
adventure                        0
album                            0
app                              0
art                              0
artist                           0
band                             0
base                             0
beautiful                        0
best                             0
book                             0
bring                            0
build                            0
card                             0
cd                               0
change                           0
child                            0
city                             0
collection                       0
come                             0
comedy                           0
comic               

In [58]:
data.shape

(157117, 419)